In [ ]:
#Game.py
import torch
import math
from copy import deepcopy
import sys
sys.setrecursionlimit(10000)
skipped = 0
skip_first = True

class Game():
    """
    This class specifies the base Game class. To define your own game, subclass
    this class and implement the functions below. This works when the game is
    two-player, adversarial and turn-based.

    Use 1 for player1 and -1 for player2.

    See othello/OthelloGame.py for an example implementation.
    """

    def __init__(self,verbose=False):
        self.verbose = verbose

    def _token(self,i):
        if i == 1:
            return 'O'
        elif i == -1:
            return 'X'
        else:
            return '0'
    def equals(self,obj1 : list,obj2 : list):
        obj1  = [str(item) for item in obj1]
        obj2 = [str(item) for item in obj2]
        obj1 = set(obj1)
        obj2 = set(obj2)
        return obj1 == obj2
    def cloneBoard(self,board):
      return [np.copy(board[0]),np.copy(board[1]),deepcopy(board[2])]

    def printBoard(self,board,player):
        board_only = board[0]
        print(self._token(int(board_only[0,0].item())),end='-'*30)
        print(self._token(int(board_only[0,1].item())),end='-'*30)
        print(self._token(int(board_only[0,2].item())))
        print('-'*10,end='')
        print(self._token(int(board_only[1,0].item())),end='-'*20)
        print(self._token(int(board_only[1,1].item())),end='-'*20)
        print(self._token(int(board_only[1,2].item())),end='-'*10 + '\n')
        print('-'*20,end='')
        print(self._token(int(board_only[2,0].item())),end='-'*10)
        print(self._token(int(board_only[2,1].item())),end='-'*10)
        print(self._token(int(board_only[2,2].item())),end='-'*20+'\n')

        print(self._token(int(board_only[0,7].item())),end='-'*9)
        print(self._token(int(board_only[1,7].item())),end='-'*9)
        print(self._token(int(board_only[2,7].item())),end='-'*21)
        print(self._token(int(board_only[2,3].item())),end='-'*9)
        print(self._token(int(board_only[1,3].item())),end='-'*9)
        print(self._token(int(board_only[0,3].item())))
        print('-'*20,end='')
        print(self._token(int(board_only[2,6].item())),end='-'*10)
        print(self._token(int(board_only[2,5].item())),end='-'*10)
        print(self._token(int(board_only[2,4].item())),end='-'*20 + '\n')
        print('-'*10,end='')
        print(self._token(int(board_only[1,6].item())),end='-'*20)
        print(self._token(int(board_only[1,5].item())),end='-'*20)
        print(self._token(int(board_only[1,4].item())),end='-'*10 + '\n')
        print(self._token(int(board_only[0,6].item())),end='-'*30)
        print(self._token(int(board_only[0,5].item())),end='-'*30)
        print(self._token(int(board_only[0,4].item())))
        print()
        data = board[1]
        print('player 1 (O) remaining cows: ',int(data[0].item()))
        print('player -1 (X) remaining cows:',int(data[4].item()))
        print('player 1 (O) just captured row?',int(data[1].item()))
        print('player -1 (X) just captured row?',int(data[5].item()))
        print('player 1 (O) cow selection:',int(data[2].item()))
        print('player -1 (X) cow selection:',int(data[6].item()))
        print('player 1 (O) placeable cows: ',int(data[3].item()))
        print('player -1 (X) placeable cows:',int(data[7].item()))
        print('game state: ', 'place tokens' if data[8] == 0 else 'move/fly tokens')
        print('available actions:', self.getValidMoves(board,player))
        print('game end?', self.getGameEnded(board,player))
    def getInitBoard(self):
        """
        Returns:
            startBoard: a representation of the board (ideally this is the form
                        that will be the input to your neural network)
        """
        board = np.zeros((3,8))
        # board[0,0] = 1
        # board[0,1] = -1
        # board[0,2] = -1
        # board[0,3] = -1
        # board[0,4] = -1
        # board[0,6] = 1
        # board[0,7] = 1
        # board[1,0] = 1
        # board[1,1] = 1
        # board[1,2] = -1
        # board[1,3] = 1
        # board[1,4] = -1
        # board[1,5] = 1
        # board[1,6] = -1
        # board[1,7] = 1
        # board[2,0] = 1
        # board[2,6] = 1
        # board[2,7] = -1

        #3 squares of 3x3 (innermost, middle, outermost)
        # metadata = torch.tensor([12,12,0,0,-1,-1,12,12,0])
        metadata = np.array([12,0,-1,12,12,0,-1,12,0])
        # board = np.array([[1., 0., 0., 0., 0., 1., 0., 0.],
        #         [0., 0., 1., 1., 0., -1., 0., 0.],
        #         [1., 0., 0., 1., -1., -1., -1., 1.]])
        # metadata = np.array([7, 0, 23, 0, 4, 0, -1, 0, 1])
        row_capture_data = {'-1':[],'1':[]}
        #this player remaining tokens = data[0],  this player row captured = data[1], this player selected cow = data[2], this player placeable tokens = data[3], game state = data[-1]
        #vector that represents each player's remaining tokens (alive, not necessarily placeable) + whether each player has just captured a row + the cow selected for moving for each player + the remaining cow tokens available to place for each players + the game phase code
        return [board, metadata, row_capture_data]

    def getBoardSize(self):
        """
        Returns:
            (x,y): a tuple of board dimensions
        """
        return (3,8)

    def getActionSize(self):
        """
        Returns:
            actionSize: number of all possible actions
        """
        return 25

    def getNextState(self, board, player, action):
        """
        Input:
            board: current board with metadata
            player: current player (1 or -1)
            action: action taken by current player

        Returns:
            nextBoard: board after applying action
            nextPlayer: player who plays in the next turn (should be -player)
        """
        board = self.cloneBoard(board)
        last_row_captured_count = board[2]

        board_only = board[0]
        data = board[1]
        row_just_captured = data[1 if player == 1 else 1+4] == 1
        can_fly = data[0 if player == 1 else 0+4] <= 3 or data[-1] == 0
        cow_selected = data[2 if player == 1 else 2+4]
        # player_index = 6 if player == 1 else 7
        game_state = data[-1]


        if action <= 23:
            if not row_just_captured and cow_selected == -1 and game_state == 0:
                #placing cow on the board
                square = min(math.ceil((action+1) / 8),3) #1st, 2nd, or 3rd square
                cell = action - 8 * (square-1)
                board_only[square-1,cell] = player
                #decrement placeable count
                data[3 if player == 1 else 3+4] -= 1
                if self.verbose:
                    print('PLACED cow on the board')

            if not row_just_captured and game_state == 1 and cow_selected == -1:
                #selecting cow to move
                data[2 if player == 1 else 2+4] = action
                if self.verbose:
                    print('SELECTED cow on the board')

                return board, player
            if row_just_captured:
                # displace opponent's cow on the board
                # action = action - 24
                square = min(math.ceil((action+1) / 8),3)
                cell = action - 8 * (square - 1)
                board_only[square-1, cell] = 0
                # decrement the other player's remaining cows
                data[4 if player == 1 else 0] -= 1
                #set row_captured to 0
                data[1 if player == 1 else 1+4] = 0
                if self.verbose:
                    print('DISPLACED cow on the board')
                #update opponent's row counts
                row_capture_count = {str(-player): [], str(player): last_row_captured_count[str(player)]}

                row_capture_count[str(-player)] = []
                horizontal_vertical_patterns = [
                    [0, 1, 2],
                    [2, 3, 4],
                    [4, 5, 6],
                    [6, 7, 0]
                ]
                # check capture within square
                for i in range(3):
                    square = board_only[i]
                    for pattern in horizontal_vertical_patterns:
                        if square[pattern[0]] == -player and square[pattern[1]] == -player and square[
                            pattern[2]] == -player:
                            # row captured!

                            captured = True
                            row_capture_count[str(-player)].append([pattern[0] * (i+1),pattern[1] * (i+1),pattern[2] * (i+1)])
                # check captures across squares
                for i in range(8):
                    if board_only[0][i] == -player and board_only[1][i] == -player and board_only[2][i] == -player:
                        # row captured!

                        captured = True
                        row_capture_count[str(-player)].append([i,i,i])

                board[2] = row_capture_count
                return board, -player
            if not row_just_captured and cow_selected != -1 and game_state == 1:
                #moving cow on the board
                square = min(math.ceil((cow_selected+1) / 8),3)
                cell = cow_selected - 8 * (square - 1)
                board_only[square-1, cell] = 0
                square = min(math.ceil((action+1) / 8),3)
                cell = action - 8 * (square - 1)
                board_only[square-1, cell] = player
                data[2 if player == 1 else 2+4] = -1
                if self.verbose:
                    print('MOVED cow on the board')
        else:
            #no action
            return board, -player

        #update game state
        if data[3] <= 0 and data[7] <= 0:
            #if both players do not have any more placeable tokens, then the game phase is updated to 1 (where only moving tokens are possible)
            data[-1] = 1
            if self.verbose:
                print('Game state updated')

        #check for any row capture on current player's side
        horizontal_vertical_patterns = [
            [0,1,2],
            [2,3,4],
            [4,5,6],
            [6,7,0]
        ]
        captured = False
        row_capture_count = { str(player) : [], str(-player) : last_row_captured_count[str(-player)]}

        row_capture_count[str(player)] = []
        #check capture within square
        for i in range(3):
            square = board_only[i]
            for pattern in horizontal_vertical_patterns:
                if square[pattern[0]] == player and square[pattern[1]] == player and square[pattern[2]] == player:
                    #row captured!

                    captured = True
                    row_capture_count[str(player)].append([pattern[0]*(i+1),pattern[1]*(i+1),pattern[2]*(i+1)])
        #check captures across squares
        for i in range(8):
            if board_only[0][i] == player and board_only[1][i] == player and board_only[2][i] == player:
                #row captured!

                captured = True
                row_capture_count[str(player)].append([i,i,i])

        if self.verbose:
            print('total row capture count (for current player):',row_capture_count[str(player)], 'last row capture count (for current player):',last_row_captured_count[str(player)])
        if captured and not self.equals(row_capture_count[str(player)],last_row_captured_count[str(player)]) and len(row_capture_count[str(player)]) >= len(last_row_captured_count[str(player)]):
            data[1 if player == 1 else 1+4] = 1
            if self.verbose:
                print('ROW CAPTURED')
            board[2] = row_capture_count
            return board, player

        board[2] = row_capture_count
        return board, -player

    def _getNeighbor(self,board,cell):
        board = self.cloneBoard(board)
        #given the a cell, return its neighboring (adjacent) cells id
        #create a dummy board...
        board_only = torch.zeros((3,8))
        #index it
        board_only[0] = torch.arange(0,8)
        board_only[1] = torch.arange(8,16)
        board_only[2] = torch.arange(16,24)
        square = min(math.ceil((cell+1)/8) , 3)
        cell = cell - 8 * (square-1)
        neighbors = []
        square = square-1
        #check for horizontal/vertical neighbors within its square
        neighbors.append(board_only[square,(cell+1) % 8])
        neighbors.append(board_only[square,(cell-1) % 8])
        #check for diagonal neighbors outside of its square
        square_neighbors = {0 : [1], 1: [0,2], 2 : [1]}
        try:
            for square_ in square_neighbors[square]:
                neighbors.append(board_only[square_,cell])

        except IndexError:
            pass

        neighbors = [int(e.item()) for e in neighbors]
        return np.array(neighbors).astype(np.uint8)



    def getValidMoves(self, board, player):
        """
        Input:
            board: current board
            player: current player

        Returns:
            validMoves: a binary vector of length self.getActionSize(), 1 for
                        moves that are valid from the current board and player,
                        0 for invalid moves
        """
        board = self.cloneBoard(board)
        board_only = board[0]
        data = board[1]
        action_vector = torch.zeros((self.getActionSize()-1,))
        #check if the player has just captured a row
        # player_index = 2 if player == 1 else 3
        # print('DATA CHECK:',data)
        captured_row = data[1] == 1
        if captured_row:
            #if a row has just been captured...
            for i in range(24):
                square = min(math.ceil((i+1)/8),3)
                cell = (i) - 8 * (square-1)
                status = board_only[square-1,cell]

                #any cow on the cell where it is occupied by the OTHER player can be displaced
                if status == -player:
                    # print('status=', status, '(',i,')')
                    action_vector[i] = 1
        else:
            #if a row has not been captured, check whether the current player can fly
            # player_index = 0 if player == 1 else 1
            can_fly = data[0] <= 3 or data[-1] == 0

            #game phase 0 (placing cow anywhere)
            if can_fly and data[-1] == 0:
                #if can fly, then any empty cell is available for the current player to place their cow on
                for i in range(24):
                    square = min(math.ceil((i+1)/8),3)
                    cell = i - 8 * (square - 1)

                    status = board_only[square-1, cell]
                    # print(square - 1, cell, i, status)
                    if status == 0:
                        action_vector[i] = 1
            #game phase 1 (moving cow anywhere)
            elif can_fly and data[-1] == 1:
                # first check if the player has selected a cow to move
                # player_index = 4 if player == 1 else 5
                cow_selected = data[2] >= 0
                if not cow_selected:
                    for i in range(24):
                        square = min(math.ceil((i+1)/8),3)
                        cell = i - 8 * (square - 1)
                        status = board_only[square-1, cell]
                        #if cow is not selected, the player must select a cow to move, and this can be any cell occupied by the current player
                        if status == player:
                            action_vector[i] = 1
                else:
                    #if cow has been selected, all empty cells are available
                    for i in range(24):
                        square = min(math.ceil((i+1)/8),3)
                        cell = i - 8 * (square - 1)
                        status = board_only[square-1, cell]
                        if status == 0:
                            action_vector[i] = 1

            else:
                #if cannot fly, then only the cells within one adjacent reach of the current player's cow are available

                #first check if the player has selected a cow to move
                # player_index = 4 if player == 1 else 5
                cow_selected = data[2] >=0
                # print('cow selected? ', cow_selected)
                if not cow_selected:
                    for i in range(24):
                        square = min(math.ceil((i+1)/8),3)
                        cell = i - 8 * (square - 1)
                        status = board_only[square-1, cell]
                        #if cow is not selected, the player must select a cow to move, and this can be any cell occupied by the current player that has a valid neighbor to move to
                        if status == player:
                            neighbors = self._getNeighbor(board_only,i)
                            for neighbor in neighbors:
                                square = min(math.ceil((neighbor + 1) / 8), 3)
                                cell = neighbor - 8 * (square - 1)
                                if board_only[square - 1, cell] == 0:
                                    action_vector[i] = 1
                                    break


                else:
                    #if cow has been selected, its neighboring cells are available
                    cow_selected = data[2]
                    neighbors = self._getNeighbor(board_only,cow_selected)
                    for neighbor in neighbors:
                        # all empty neighbors == available action
                        square = min(math.ceil((neighbor + 1) / 8), 3)
                        cell = neighbor - 8 * (square - 1)
                        if board_only[square-1,cell] == 0:
                            action_vector[neighbor] = 1
        no_action = torch.zeros(size=(1,))
        if action_vector.sum() < 0.001:
            no_action[0] = 1
        action_vector = torch.cat([action_vector,no_action],dim=0)
        return action_vector.detach().numpy()









    def getGameEnded(self, board, player):
        """
        Input:
            board: current board
            player: current player (1 or -1)

        Returns:
            r: 0 if game has not ended. 1 if player won, -1 if player lost,
               small non-zero value for draw.

        """
        board = self.cloneBoard(board)
        data = board[1]
        remaining_tokens = data[0 if player == 1 else 4]
        remaining_tokens_other = data[4 if player == 1 else 0]

        win = remaining_tokens_other <= 2
        if win:
            return 1
        loss = remaining_tokens <= 2
        if loss:
            return -1
          

        if remaining_tokens == 12 and remaining_tokens_other == 12 and data[3] == 0 and data[7] == 0:
            return 0.1 #could rarely happen for a draw!
        if (remaining_tokens == 12 and remaining_tokens_other == 11) or (remaining_tokens == 11 and remaining_tokens_other == 12) and data[3] == 0 and data[7] == 0:
            return 0.1 #this would return never ending cycle
        if remaining_tokens == 3 and remaining_tokens_other == 3:
          return 0.1 #could be considered draw as this could go on forever
        return 0

    def getCanonicalForm(self, board, player):
        """
        Input:
            board: current board
            player: current player (1 or -1)

        Returns:
            canonicalBoard: returns canonical form of board. The canonical form
                            should be independent of player. For e.g. in chess,
                            the canonical form can be chosen to be from the pov
                            of white. When the player is white, we can return
                            board as is. When the player is black, we can invert
                            the colors and return the board.
        """

        board = self.cloneBoard(board)
        if player == 1:
            return board
        else:
            board[0] = board[0] * -1
            data = board[1]
            board[1] = np.array(
                [data[4], data[5], data[6], data[7], data[0], data[1], data[2], data[3], data[-1]])
            return board

    def getSymmetries(self, board, pi):
        """
        Input:
            board: current board
            pi: policy vector of size self.getActionSize()

        Returns:
            symmForms: a list of [(board,pi)] where each tuple is a symmetrical
                       form of the board and the corresponding pi vector. This
                       is used when training the neural network from examples.
        """
        pass

    def stringRepresentation(self, board):
        """
        Input:
            board: current board

        Returns:
            boardString: a quick conversion of board to a string format.
                         Required by MCTS for hashing.
        """
        board = self.getCanonicalForm(board,1)
        boardString = ""
        board_only = board[0]
        for i in range(24):
            square = min(math.ceil((i+1)/8),3)
            cell = i - 8 * (square - 1)
            boardString += str(board_only[square-1,cell]) + ','
        data = board[1]
        for datum in data:
            boardString += str(datum) + ','

        return boardString



def play():
    game = Game()
    player = 1
    board = game.getInitBoard()


    last_row_captured_count = {'-1': [], '1': []}

    while True:
        game.printBoard(board,player)
        print('player',player,'\'s turn')
        valid_moves = game.getValidMoves(board,player)
        if valid_moves.sum() < 0.001:
            print('no valid moves for player',player,'; skipping turn.')
            player = -player
            continue
        action = int(input('Type action: (0-24), from outer square to inner square clockwise from top left corner:\n'))
        if action > 24 or action < 0 or valid_moves[action] == 0:
            print('Invalid action! try again!')
            continue
        board, player  = game.getNextState(board,player,action)
        end = game.getGameEnded(board,player)
        if end != 0:
            print('Game ended with a reward of ',end,'for player',player)
            break


#Arena.py



import logging

from tqdm import tqdm
import numpy as np
import torch
import math




class Arena():
    """
    An Arena class where any 2 agents can be pit against each other.
    """

    def __init__(self, player1, player2, game, display=None):
        """
        Input:
            player 1,2: two functions that takes board as input, return action
            game: Game object
            display: a function that takes board as input and prints it (e.g.
                     display in othello/OthelloGame). Is necessary for verbose
                     mode.

        see othello/OthelloPlayers.py for an example. See pit.py for pitting
        human players/other baselines with each other.
        """
        self.player1 = player1
        self.player2 = player2
        self.game = game
        self.display = display
        self.last_row_captured_count = {'1' : [], '-1': []}
        self.max_it = 10000

    def playGame(self, verbose=False):
        """
        Executes one episode of a game.

        Returns:
            either
                winner: player who won the game (1 if player1, -1 if player2)
            or
                draw result returned from the game that is neither 1, -1, nor 0.
        """
        verbose = False
        self.display = self.game.printBoard
        players = [self.player2, None, self.player1]
        curPlayer = 1
        board = self.game.getInitBoard()
        it = 0
        while self.game.getGameEnded(board, curPlayer) == 0 and it <= self.max_it:
            it += 1
            if verbose:
                assert self.display
                print("Turn ", str(it), "Player ", str(curPlayer))
                self.display(board,curPlayer)

            valids = self.game.getValidMoves(self.game.getCanonicalForm(board, curPlayer), 1)
            # print('valids=', valids)
            # print('other(actual) valids=', self.game.getValidMoves(board,curPlayer))
            action = players[curPlayer + 1](self.game.getCanonicalForm(board, curPlayer))


            # print('action chosen=',action)

            if valids[action] == 0:
                log.error(f'Action {action} is not valid!')
                log.debug(f'valids = {valids}')
                assert valids[action] > 0
            board, curPlayer = self.game.getNextState(board, curPlayer, action)
        if verbose:
            assert self.display
            print("Game over: Turn ", str(it), "Result ", str(self.game.getGameEnded(board, 1)))
            self.display(board,curPlayer)
        print('Game end at perpective of player',curPlayer)
        return curPlayer * self.game.getGameEnded(board, curPlayer)

    def playGames(self, num, verbose=False):
        """
        Plays num games in which player1 starts num/2 games and player2 starts
        num/2 games.

        Returns:
            oneWon: games won by player1
            twoWon: games won by player2
            draws:  games won by nobody
        """

        num = int(num / 2)
        oneWon = 0
        twoWon = 0
        draws = 0
        for _ in tqdm(range(num), desc="Arena.playGames (1)"):
            gameResult = self.playGame(verbose=verbose)
            if gameResult == 1:
                oneWon += 1
                print('player 1 wins')
            elif gameResult == -1:
                twoWon += 1
                print('player 2 wins')
            else:
                draws += 1
                print('draw')

        self.player1, self.player2 = self.player2, self.player1

        for _ in tqdm(range(num), desc="Arena.playGames (2)"):
            gameResult = self.playGame(verbose=verbose)
            if gameResult == -1:
                oneWon += 1
                print('player 1 wins')
            elif gameResult == 1:
                twoWon += 1
                print('player 2 wins')
            else:
                draws += 1
                print('draw')

        return oneWon, twoWon, draws


def random_agent(board,valid_moves):
    options = []
    for i, action_valid in enumerate(valid_moves):
        if action_valid == 1:
            options.append(i)

    action = np.random.choice(options)
    return action

# valids = torch.tensor([0., 0., 0., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 1., 0.,
#         0., 0., 0., 1., 1., 0.])

# for _ in range(50):
#     print(random_agent(None,valids))

# game = Game()
#
# for i in range(24):
#     print(f'neighbor for {i}',game._getNeighbor(game.getInitBoard()[0],i))
# arena = Arena(player1=random_agent,player2=random_agent,game=Game(),display=game.printBoard)
#
# arena.playGame(verbose=True)
# oneWon, twoWon, draw = arena.playGames(num=25,verbose=True)
# print('-------')
# print('stats:')
# print('oneWon:',oneWon)
# print('twoWon:',twoWon)
# print('draws:',draw)

# board = (torch.tensor([1,1,1,1,1]),torch.tensor([0,0,0]))
# board_ = [torch.clone(board[0]),torch.clone(board[1])]
#
# board_[0] = -1 * board_[0]
#
# print(board_)
# print(board)

#ZuluNnet.py
import argparse
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

class ZuluNNet(nn.Module):
    def __init__(self,game,args):
        self.board_x, self.board_y = 7, 7
        self.action_size = game.getActionSize()
        self.args = args
        super(ZuluNNet,self).__init__()
        self.conv1 = nn.Conv2d(1,args.num_channels,3,stride=1,padding=1)
        self.conv2 = nn.Conv2d(args.num_channels,args.num_channels,3,stride=1,padding=1)
        self.conv3 = nn.Conv2d(args.num_channels,args.num_channels,3,stride=1)
        self.conv4 = nn.Conv2d(args.num_channels,args.num_channels,3,stride=1)
        self.conv5 = nn.Conv2d(args.num_channels,args.num_channels,3,stride=1,padding='same')

        self.bn1 = nn.BatchNorm2d(args.num_channels)
        self.bn2 = nn.BatchNorm2d(args.num_channels)
        self.bn3 = nn.BatchNorm2d(args.num_channels)
        self.bn4 = nn.BatchNorm2d(args.num_channels)
        self.bn5 = nn.BatchNorm2d(args.num_channels)
        self.bn_metadata_1 = nn.BatchNorm1d(64)

        self.fc_metadata_1 = nn.Linear(args.num_metadata, 64)

        # print('channels=',args.num_channels * (self.board_x) * (self.board_y))
        self.fc1 = nn.Linear(args.num_channels * (self.board_x-4) * (self.board_y-4) + 64, 1024)
        self.fc_bn1 = nn.BatchNorm1d(1024)

        self.fc2 = nn.Linear(1024,512)
        self.fc_bn2 = nn.BatchNorm1d(512)

        self.fc3 = nn.Linear(512,self.action_size)

        self.fc4 = nn.Linear(512,1)
        self.flat_dim = args.num_channels * (self.board_x-4) * (self.board_y-4)


    def span(self,s_):
        #s shape (batch,3,8)
        stack = []
        for s in s_:
            spanned_board = [[s[0, 0], 0, 0, s[0, 1], 0, 0, s[0, 2]],
                             [0, s[1, 0], 0, s[1, 1], 0, s[1, 2], 0],
                             [0, 0, s[2, 0], s[2, 1], s[2, 2], 0, 0],
                             [s[0, 7], s[1, 7], s[2, 7], 0, s[2, 3], s[1, 3], s[0, 3]],
                             [0, 0, s[2, 6], s[2, 5], s[2, 4], 0, 0],
                             [0, s[1, 6], 0, s[1, 5], 0, s[1, 4], 0],
                             [s[0, 6], 0, 0, s[0, 5], 0, 0, s[0, 4]]]
            stack.append(torch.FloatTensor(spanned_board))

        spanned_board = torch.stack(stack,dim=0)

        if args.cuda:
          spanned_board = spanned_board.contiguous().cuda()

        return spanned_board

    def forward(self,s,data):
        #s shape: (batch,3,8)
        s = self.span(s) #s shape : (7,7)
        s = s.view(-1,1,self.board_x,self.board_y)
        s = F.relu(self.bn1(self.conv1(s)))
        s = F.relu(self.bn2(self.conv2(s)))
        s = F.relu(self.bn3(self.conv3(s)))
        s = F.relu(self.bn4(self.conv4(s)))
        s = F.relu(self.bn5(self.conv5(s)))

        s = s.view(-1,self.flat_dim)
        data = F.relu(self.bn_metadata_1(self.fc_metadata_1(data)))
        s = torch.concat([s,data],dim=-1)
        s = F.dropout(F.relu(self.fc_bn1(self.fc1(s))), p=self.args.dropout,
                      training=self.training)
        s = F.dropout(F.relu(self.fc_bn2(self.fc2(s))), p=self.args.dropout, training=self.training)  # batch_size x 512

        pi = self.fc3(s)
        v = self.fc4(s)

        return F.log_softmax(pi,dim=1), torch.tanh(v)

#NNet.py

import os
import sys
import time
import numpy as np
from tqdm import tqdm

import torch
import torch.optim

class NeuralNet():
    """
    This class specifies the base NeuralNet class. To define your own neural
    network, subclass this class and implement the functions below. The neural
    network does not consider the current player, and instead only deals with
    the canonical form of the board.

    See othello/NNet.py for an example implementation.
    """

    def __init__(self, game, args):
        self.nnet = ZuluNNet(game,args)
        self.board_x, self.board_y = game.getBoardSize()
        self.action_size = game.getActionSize()
        if args.cuda:
            self.nnet.cuda()
        self.args = args


    def train(self, examples):
        """
        This function trains the neural network with examples obtained from
        self-play.

        Input:
            examples: a list of training examples, where each example is of form
                      (board, pi, v). pi is the MCTS informed policy vector for
                      the given board, and v is its value. The examples has
                      board in its canonical form.
        """
        optimizer = torch.optim.Adam(self.nnet.parameters())
        for epoch in range(self.args.epochs):
            print('EPOCH ', str(epoch+1))
            self.nnet.train()
            batch_n = int(len(examples) / self.args.batch_size)
            print('batch count=',batch_n)

            for i in range(batch_n):
                sample_ids = np.random.randint(len(examples),size=self.args.batch_size)
                boards, pis, vs = list(zip(*[examples[i] for i in sample_ids]))

                boards_only = [e[0] for e in boards]
                data = [e[1] for e in boards]
                boards = boards_only
                
                boards = torch.FloatTensor(np.array(boards).astype(np.float64))
                data = torch.FloatTensor(np.array(data).astype(np.float64))

                target_pis = torch.FloatTensor(np.array(pis))
                target_vs = torch.FloatTensor(np.array(vs).astype(np.float64))
                if self.args.cuda:
                    boards, target_pis, target_vs = boards.contiguous().cuda(), target_pis.contiguous().cuda(), target_vs.contiguous().cuda()
                    data = data.contiguous().cuda()
                out_pi, out_v = self.nnet(boards,data)
                l_pi = self.loss_pi(target_pis,out_pi)
                l_v = self.loss_v(target_vs,out_v)
                total_loss = l_pi + l_v
                
                optimizer.zero_grad()
                total_loss.backward()
                optimizer.step()
                print(f'training batch {i}/{batch_n} total loss {total_loss}')

    def predict(self, board):
        """
        Input:
            board: current board in its canonical form.

        Returns:
            pi: a policy vector for the current board- a numpy array of length
                game.getActionSize
            v: a float in [-1,1] that gives the value of the current board
        """
        data = board[1]
        board = board[0]
        board = torch.FloatTensor(board.astype(np.float64))
        data = torch.FloatTensor(data.astype(np.float64)).unsqueeze(0)
        if self.args.cuda:
            board = board.contiguous().cuda()
            data = data.contiguous().cuda()
        board = board.view(1,self.board_x,self.board_y)
        self.nnet.eval()

        with torch.no_grad():
            pi, v = self.nnet(board,data)

        return torch.exp(pi).data.cpu().numpy()[0], v.data.cpu().numpy()[0]

    def loss_pi(self,targets,outputs):
        return -torch.sum(targets * outputs) / targets.size()[0]
    def loss_v(self,targets,outputs):
        return torch.sum((targets - outputs.view(-1)) ** 2) / targets.size()[0]

    def save_checkpoint(self, folder='checkpoint', filename='checkpoint.pth.tar'):
        filepath = os.path.join(folder, filename)
        if not os.path.exists(folder):
            print("Checkpoint Directory does not exist! Making directory {}".format(folder))
            os.mkdir(folder)
        else:
            print("Checkpoint Directory exists! ")
        torch.save({
            'state_dict': self.nnet.state_dict(),
        }, filepath)

    def load_checkpoint(self, folder='checkpoint', filename='checkpoint.pth.tar'):
        # https://github.com/pytorch/examples/blob/master/imagenet/main.py#L98
        filepath = os.path.join(folder, filename)
        if not os.path.exists(filepath):
            raise ("No model in path {}".format(filepath))
        map_location = None if self.args.cuda else 'cpu'
        checkpoint = torch.load(filepath, map_location=map_location)
        self.nnet.load_state_dict(checkpoint['state_dict'])

#MCTS.py
import logging
import math

import numpy as np

EPS = 1e-8

logging.basicConfig(filename="newfile.log",
                    format='%(asctime)s %(message)s',
                    filemode='w')
log = logging.getLogger(__name__)




class MCTS():
    """
    This class handles the MCTS tree.
    """

    def __init__(self, game, nnet, args):
        self.game = game
        self.nnet = nnet
        self.args = args
        self.Qsa = {}  # stores Q values for s,a (as defined in the paper)
        self.Nsa = {}  # stores #times edge s,a was visited
        self.Ns = {}  # stores #times board s was visited
        self.Ps = {}  # stores initial policy (returned by neural net)

        self.Es = {}  # stores game.getGameEnded ended for board s
        self.Vs = {}  # stores game.getValidMoves for board s


    def getActionProb(self, canonicalBoard, temp=1):
      
        """
        This function performs numMCTSSims simulations of MCTS starting from
        canonicalBoard.

        Returns:
            probs: a policy vector where the probability of the ith action is
                   proportional to Nsa[(s,a)]**(1./temp)
        """
        global skipped
        for i in range(self.args.numMCTSSims):
          try:
            self.search(canonicalBoard)
          except RecursionError:
            print('oof,', canonicalBoard)
            print('skipping this state')

            skipped += 1

            #select any random uniform valid action
            counts = self.game.getValidMoves(canonicalBoard,1)
            bestAs = np.array(np.argwhere(counts == np.max(counts))).flatten()
            bestA = np.random.choice(bestAs)
            probs = [0] * len(counts)
            probs[bestA] = 1
            return probs
            

        s = self.game.stringRepresentation(canonicalBoard)
        # print('query string=',s)
        counts = [self.Nsa[(s, a)] if (s, a) in self.Nsa else 0 for a in range(self.game.getActionSize())]
        # print('counts=',counts)
        # for s, a in self.Nsa.keys():
        #   print((s,a) , self.Nsa[(s,a)])
        if temp == 0:
            bestAs = np.array(np.argwhere(counts == np.max(counts))).flatten()
            bestA = np.random.choice(bestAs)
            probs = [0] * len(counts)
            probs[bestA] = 1
            return probs

        counts = [x ** (1. / temp) for x in counts]
        counts_sum = float(sum(counts))
        probs = [x / counts_sum for x in counts]
        return probs

    def search(self, canonicalBoard,verbose=False):
        """
        This function performs one iteration of MCTS. It is recursively called
        till a leaf node is found. The action chosen at each node is one that
        has the maximum upper confidence bound as in the paper.

        Once a leaf node is found, the neural network is called to return an
        initial policy P and a value v for the state. This value is propagated
        up the search path. In case the leaf node is a terminal state, the
        outcome is propagated up the search path. The values of Ns, Nsa, Qsa are
        updated.

        NOTE: the return values are the negative of the value of the current
        state. This is done since v is in [-1,1] and if v is the value of a
        state for the current player, then its value is -v for the other player.

        Returns:
            v: the negative of the value of the current canonicalBoard
        """

        # print('search called:',canonicalBoard)

        if verbose:
          print('search called=',canonicalBoard)
        s = self.game.stringRepresentation(canonicalBoard)

        if s not in self.Es:
            self.Es[s] = self.game.getGameEnded(canonicalBoard, 1)
        if self.Es[s] != 0:
            # terminal node
            return -self.Es[s]

        if s not in self.Ps:
            # leaf node
            self.Ps[s], v = self.nnet.predict(canonicalBoard)
            valids = self.game.getValidMoves(canonicalBoard, 1)

            self.Ps[s] = self.Ps[s] * valids  # masking invalid moves
            sum_Ps_s = np.sum(self.Ps[s])
            if sum_Ps_s > 0:
                self.Ps[s] /= sum_Ps_s  # renormalize
            else:
                # if all valid moves were masked make all valid moves equally probable

                # NB! All valid moves may be masked if either your NNet architecture is insufficient or you've get overfitting or something else.
                # If you have got dozens or hundreds of these messages you should pay attention to your NNet and/or training process.
                log.error("All valid moves were masked, doing a workaround.")
                self.Ps[s] = self.Ps[s] + valids
                self.Ps[s] /= np.sum(self.Ps[s])
              

            self.Vs[s] = valids
            self.Ns[s] = 0
            return -v

        valids = self.Vs[s]
        cur_best = -float('inf')
        best_act = -1

        # pick the action with the highest upper confidence bound
        for a in range(self.game.getActionSize()):
            if valids[a]:
                if (s, a) in self.Qsa:
                    u = self.Qsa[(s, a)] + self.args.cpuct * self.Ps[s][a] * math.sqrt(self.Ns[s]) / (
                            1 + self.Nsa[(s, a)])
                else:
                    u = self.args.cpuct * self.Ps[s][a] * math.sqrt(self.Ns[s] + EPS)  # Q = 0 ?

                if u > cur_best:
                    cur_best = u
                    best_act = a

        a = best_act
        next_s, next_player = self.game.getNextState(canonicalBoard, 1, a)
        next_s = self.game.getCanonicalForm(next_s, next_player)

        v = self.search(next_s,verbose=verbose)

        if (s, a) in self.Qsa:
            self.Qsa[(s, a)] = (self.Nsa[(s, a)] * self.Qsa[(s, a)] + v) / (self.Nsa[(s, a)] + 1)
            self.Nsa[(s, a)] += 1

        else:
            self.Qsa[(s, a)] = v
            self.Nsa[(s, a)] = 1

        self.Ns[s] += 1
        return -v

#Coach.py
import logging
import os
import sys
from collections import deque
from pickle import Pickler, Unpickler
from random import shuffle

import numpy as np
from tqdm import tqdm




class Coach():
    """
    This class executes the self-play + learning. It uses the functions defined
    in Game and NeuralNet. args are specified in main.py.
    """

    def __init__(self, game, nnet, args):
        self.game = game
        self.nnet = nnet
        self.pnet = self.nnet.__class__(self.game,args)  # the competitor network
        self.args = args
        self.mcts = MCTS(self.game, self.nnet, self.args)
        self.trainExamplesHistory = []  # history of examples from args.numItersForTrainExamplesHistory latest iterations
        self.skipFirstSelfPlay = False  # can be overriden in loadTrainExamples()

    def executeEpisode(self,n=0):
        """
        This function executes one episode of self-play, starting with player 1.
        As the game is played, each turn is added as a training example to
        trainExamples. The game is played till the game ends. After the game
        ends, the outcome of the game is used to assign values to each example
        in trainExamples.

        It uses a temp=1 if episodeStep < tempThreshold, and thereafter
        uses temp=0.

        Returns:
            trainExamples: a list of examples of the form (canonicalBoard, currPlayer, pi,v)
                           pi is the MCTS informed policy vector, v is +1 if
                           the player eventually won the game, else -1.
        """
        trainExamples = []
        board = self.game.getInitBoard()
        self.curPlayer = 1
        episodeStep = 0
        global skipped

        while True:
            episodeStep += 1
            canonicalBoard = self.game.getCanonicalForm(board, self.curPlayer)
            self.game.printBoard(board,self.curPlayer)
            temp = int(episodeStep < self.args.tempThreshold)

            pi = self.mcts.getActionProb(canonicalBoard, temp=temp)
            # sym = self.game.getSymmetries(canonicalBoard, pi)
            # for b, p in sym:
            #     trainExamples.append([b, self.curPlayer, p, None])
            trainExamples.append([canonicalBoard,self.curPlayer,pi,None])

            action = np.random.choice(len(pi), p=pi)
            # print('pi=',pi)
            # print('action taken=',action)
            board, self.curPlayer = self.game.getNextState(board, self.curPlayer, action)

            r = self.game.getGameEnded(board, self.curPlayer)
            print(f'Total skipped {skipped} Episode {n}','Running episode step at executeEpisode()',episodeStep)

            if r != 0:
                return [(x[0], x[2], r * ((-1) ** (x[1] != self.curPlayer))) for x in trainExamples]

    def learn(self):
        """
        Performs numIters iterations with numEps episodes of self-play in each
        iteration. After every iteration, it retrains neural network with
        examples in trainExamples (which has a maximum length of maxlenofQueue).
        It then pits the new neural network against the old one and accepts it
        only if it wins >= updateThreshold fraction of games.
        """

        global skip_first
        for i in range(1, self.args.numIters + 1):
            if i == 1:
              skip_first = True
              print('skipping first iteration episode collection')
            else:
              skip_first = False
              
            # bookkeeping
            if not skip_first:
              skip_first = False
              log.info(f'Starting Iter #{i} ...')
              # examples of the iteration
              if not self.skipFirstSelfPlay or i > 1:
                  iterationTrainExamples = deque([], maxlen=self.args.maxlenOfQueue)

                  for j in tqdm(range(self.args.numEps), desc="Self Play"):
                    
                      self.mcts = MCTS(self.game, self.nnet, self.args)  # reset search tree
                      iterationTrainExamples += self.executeEpisode(n=j)

                  # save the iteration examples to the history
                  self.trainExamplesHistory.append(iterationTrainExamples)

              if len(self.trainExamplesHistory) > self.args.numItersForTrainExamplesHistory:
                  log.warning(
                      f"Removing the oldest entry in trainExamples. len(trainExamplesHistory) = {len(self.trainExamplesHistory)}")
                  self.trainExamplesHistory.pop(0)
              # backup history to a file
              # NB! the examples were collected using the model from the previous iteration, so (i-1)
              self.saveTrainExamples(i - 1)

            # shuffle examples before training
            trainExamples = []
            for e in self.trainExamplesHistory:
                trainExamples.extend(e)
            shuffle(trainExamples)

            # training new network, keeping a copy of the old one
            self.nnet.save_checkpoint(folder=self.args.checkpoint, filename='temp.pth.tar')
            self.pnet.load_checkpoint(folder=self.args.checkpoint, filename='temp.pth.tar')
            pmcts = MCTS(self.game, self.pnet, self.args)

            self.nnet.train(trainExamples)
            nmcts = MCTS(self.game, self.nnet, self.args)

            print('PITTING AGAINST PREVIOUS VERSION')
            arena = Arena(lambda x: np.argmax(pmcts.getActionProb(x, temp=0)),
                          lambda x: np.argmax(nmcts.getActionProb(x, temp=0)), self.game)
            pwins, nwins, draws = arena.playGames(self.args.arenaCompare,verbose=True)

            print('NEW/PREV WINS : %d / %d ; DRAWS : %d' % (nwins, pwins, draws))
            if pwins + nwins == 0 or float(nwins) / (pwins + nwins) < self.args.updateThreshold:
                print('REJECTING NEW MODEL')
                self.nnet.load_checkpoint(folder=self.args.checkpoint, filename='temp.pth.tar')
            else:
                print('ACCEPTING NEW MODEL')
                self.nnet.save_checkpoint(folder=self.args.checkpoint, filename=self.getCheckpointFile(i))
                self.nnet.save_checkpoint(folder=self.args.checkpoint, filename='best.pth.tar')

    def getCheckpointFile(self, iteration):
        return 'checkpoint_' + str(iteration) + '.pth.tar'

    def saveTrainExamples(self, iteration):
        folder = self.args.checkpoint
        if not os.path.exists(folder):
            os.makedirs(folder)
        filename = os.path.join(folder, self.getCheckpointFile(iteration) + ".examples")
        with open(filename, "wb+") as f:
            Pickler(f).dump(self.trainExamplesHistory)
        f.closed

    def loadTrainExamples(self):
        # modelFile = os.path.join(self.args.load_folder_file[0], self.args.load_folder_file[1])
        modelFile = os.path.join('drive/MyDrive/zulu_temp','checkpoint_0.pth.tar')
        examplesFile = modelFile + ".examples"
        if not os.path.isfile(examplesFile):
            log.warning(f'File "{examplesFile}" with trainExamples not found!')
            r = input("Continue? [y|n]")
            if r != "y":
                sys.exit()
        else:
            log.info("File with trainExamples found. Loading it...")
            with open(examplesFile, "rb") as f:
                self.trainExamplesHistory = Unpickler(f).load()
            log.info('Loading done!')

            # examples based on the model were already collected (loaded)
            self.skipFirstSelfPlay = True


# args = dotdict({
#     'numIters': 1000,
#     'numEps': 100,              # Number of complete self-play games to simulate during a new iteration.
#     'tempThreshold': 15,        #
#     'updateThreshold': 0.6,     # During arena playoff, new neural net will be accepted if threshold or more of games are won.
#     'maxlenOfQueue': 200000,    # Number of game examples to train the neural networks.
#     'numMCTSSims': 25,          # Number of games moves for MCTS to simulate.
#     'arenaCompare': 40,         # Number of games to play during arena play to determine if new net will be accepted.
#     'cpuct': 1,
#
#     'checkpoint': './temp/',
#     'load_model': False,
#     'load_folder_file': ('/dev/models/8x100x50','best.pth.tar'),
#     'numItersForTrainExamplesHistory': 20,
#
# })
# args = dotdict({
#     'lr': 0.001,
#     'dropout': 0.3,
#     'epochs': 10,
#     'batch_size': 64,
#     'cuda': torch.cuda.is_available(),
#     'num_channels': 512,
# })

class Args:
    def __init__(self):
        self.lr = 0.001
        self.dropout = 0.3
        self.epochs = 10
        self.batch_size = 64
        self.cuda = torch.cuda.is_available()
        self.num_channels = 512
        self.numIters = 1000
        self.numEps = 100
        self.tempThreshold = 15
        self.updateThreshold = 0.6
        self.maxlenOfQueue = 200000
        self.numMCTSSims = 30
        self.arenaCompare = 40
        self.cpuct = 1
        self.checkpoint = './drive/MyDrive/zulu_temp/'
        self.load_model = True
        self.load_folder_file = ('./drive/MyDrive/zulu_models','best.pth.tar')
        self.numItersForTrainExamplesHistory = 20
        self.num_metadata = 9


args = Args()


def main():
    log.info('Loading %s...', Game.__name__)
    g = Game()

    log.info('Loading %s...', NeuralNet.__name__)
    nnet = NeuralNet(g,args)

    # if args.load_model:
    #     log.info('Loading checkpoint "%s/%s"...', args.load_folder_file[0], args.load_folder_file[1])
    #     nnet.load_checkpoint(args.load_folder_file[0], args.load_folder_file[1])
    # else:
    #     log.warning('Not loading a checkpoint!')

    log.info('Loading the Coach...')
    c = Coach(g, nnet, args)

    if args.load_model:
        log.info("Loading 'trainExamples' from file...")
        c.loadTrainExamples()

    log.info('Starting the learning process 🎉')
    c.learn()

main()

# net = ZuluNNet(Game(),args)

# out = net(torch.zeros((10,3,8)),torch.zeros((10,9)))
#
# print(out)

skipping first iteration episode collection
Checkpoint Directory exists! 
EPOCH  1
batch count= 232
training batch 0/232 total loss 4.294075012207031
training batch 1/232 total loss 3.896930694580078
training batch 2/232 total loss 3.7457497119903564
training batch 3/232 total loss 3.814910650253296
training batch 4/232 total loss 4.033705234527588
training batch 5/232 total loss 3.685638666152954
training batch 6/232 total loss 3.7788758277893066
training batch 7/232 total loss 3.7570714950561523
training batch 8/232 total loss 3.7464890480041504
training batch 9/232 total loss 3.6948354244232178
training batch 10/232 total loss 3.6520752906799316
training batch 11/232 total loss 3.4104418754577637
training batch 12/232 total loss 3.7044296264648438
training batch 13/232 total loss 3.806469440460205
training batch 14/232 total loss 3.5460104942321777
training batch 15/232 total loss 3.5360512733459473
training batch 16/232 total loss 3.5854337215423584
training batch 17/232 total loss

Arena.playGames (1):   5%|▌         | 1/20 [00:28<09:02, 28.55s/it]

Game end at perpective of player -1
player 1 wins
oof, [array([[-0., -1., -0.,  1., -1.,  1.,  1.,  1.],
       [-1., -0., -1.,  1.,  1., -0., -1., -0.],
       [-0.,  1., -0., -1., -1., -0.,  1.,  1.]]), array([ 9,  0,  5,  0,  7,  0, -1,  0,  1]), {'1': [], '-1': []}]
skipping this state
oof, [array([[-0., -1., -0.,  1., -1., -0.,  1.,  1.],
       [-1., -0., -1.,  1.,  1.,  1., -1., -0.],
       [-0.,  1., -1., -0., -1., -0.,  1.,  1.]]), array([ 9,  0, -1,  0,  7,  0, -1,  0,  1]), {'1': [], '-1': []}]
skipping this state
oof, [array([[ 1., -1., -0.,  1., -1.,  1., -0., -0.],
       [-1., -0., -0., -0.,  1.,  1., -0., -1.],
       [ 1., -1.,  1., -0., -0., -1.,  1., -0.]]), array([ 8,  0,  0,  0,  6,  0, -1,  0,  1]), {'1': [], '-1': []}]
skipping this state
oof, [array([[-0., -1., -0.,  1., -1.,  1., -0.,  1.],
       [-1., -0., -0., -0.,  1.,  1., -0., -1.],
       [ 1., -1.,  1., -0., -1., -0.,  1., -0.]]), array([ 8,  0, -1,  0,  6,  0, -1,  0,  1]), {'1': [], '-1': []}]
skippi

Arena.playGames (1):  10%|█         | 2/20 [01:48<17:42, 59.00s/it]

Game end at perpective of player 1
player 2 wins


...

Total skipped 491 Episode 52 Running episode step at executeEpisode() 14
0------------------------------X------------------------------0
----------0--------------------O--------------------O----------
--------------------X----------0----------0--------------------
0---------0---------O---------------------O---------X---------0
--------------------X----------O----------X--------------------
----------0--------------------O--------------------0----------
0------------------------------O------------------------------0

player 1 (O) remaining cows:  12
player -1 (X) remaining cows: 11
player 1 (O) just captured row? 0
player -1 (X) just captured row? 0
player 1 (O) cow selection: -1
player -1 (X) cow selection: -1
player 1 (O) placeable cows:  5
player -1 (X) placeable cows: 6
game state:  place tokens
available actions: [1. 0. 1. 1. 1. 0. 1. 1. 1. 0. 0. 0. 1. 0. 1. 1. 0. 1. 1. 0. 0. 0. 0. 0.
 0.]
game end? 0
Total skipped 491 Episode 52 Running episode step at executeEpisode() 15
0-------

Self Play:  54%|█████▍    | 54/100 [08:49<04:03,  5.29s/it]

Total skipped 491 Episode 53 Running episode step at executeEpisode() 14
0------------------------------0------------------------------0
----------0--------------------0--------------------0----------
--------------------0----------0----------0--------------------
0---------0---------0---------------------0---------0---------0
--------------------0----------0----------0--------------------
----------0--------------------0--------------------0----------
0------------------------------0------------------------------0

player 1 (O) remaining cows:  12
player -1 (X) remaining cows: 12
player 1 (O) just captured row? 0
player -1 (X) just captured row? 0
player 1 (O) cow selection: -1
player -1 (X) cow selection: -1
player 1 (O) placeable cows:  12
player -1 (X) placeable cows: 12
game state:  place tokens
available actions: [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 0.]
game end? 0
Total skipped 491 Episode 54 Running episode step at executeEpisode() 1
0------

Self Play:  55%|█████▌    | 55/100 [08:52<03:24,  4.54s/it]

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.

player 1 (O) remaining cows:  7
player -1 (X) remaining cows: 5
player 1 (O) just captured row? 0
player -1 (X) just captured row? 0
player 1 (O) cow selection: 13
player -1 (X) cow selection: -1
player 1 (O) placeable cows:  0
player -1 (X) placeable cows: 0
game state:  move/fly tokens
available actions: [0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0.]
game end? 0
Total skipped 509 Episode 55 Running episode step at executeEpisode() 1302
0------------------------------0------------------------------O
----------0--------------------X--------------------0----------
--------------------0----------O----------X--------------------
O---------O---------0---------------------0---------0---------0
--------------------0----------X----------O--------------------
----------0--------------------0--------------------O----------
X------------------------------O------------------------------X

player 1 (O) remaining cows:  7
player -1